In [1]:
import csv
import itertools
import os
import pickle
import random
import re
from io import open
import math

import spacy
from spacy import displacy
from conllu import parse_incr, TokenList
#from spacy_conll import init_parser
#from spacy_conll.parser import ConllParser
from tqdm.notebook import tqdm
from tqdm.contrib.concurrent import process_map

In [2]:
def get_id(input_string):
    match = re.search(r'\d+$', input_string)
    return int(match.group()) if match else -1

In [3]:
ud_hdt_sentences = {}
all_ud_hdt_sentences = []
faulty_sentences = {}
filepath = "../../libs/UD_German-HDT"
#nlp_conll = ConllParser(init_parser("de_core_news_sm", "spacy"))
for filename in tqdm(list(os.listdir("../../libs/UD_German-HDT"))):
    cur_sentences = []
    if filename.endswith('.conllu'):
        #for token_list in nlp_conll.parse_conll_file_as_spacy(os.path.join(filepath, filename)):
        #    cur_sentences.append(token_list)
        #ud_hdt_sentences[filename] = cur_sentences
        #all_ud_hdt_sentences += cur_sentences
            
        data_file = open(os.path.join(filepath, filename), "r", encoding="utf-8")
        for token_list in parse_incr(data_file):
            cur_sentences.append(token_list)
        ud_hdt_sentences[filename] = cur_sentences
        all_ud_hdt_sentences += cur_sentences
        
ud_hdt_sentences

  0%|          | 0/12 [00:00<?, ?it/s]

{'de_hdt-ud-dev.conllu': [TokenList<Konkursgerüchte, drücken, Kurs, der, Amazon-Aktie, metadata={sent_id: "hdt-s1", text: "Konkursgerüchte drücken Kurs der Amazon-Aktie"}>,
  TokenList<Begleitet, von, Marktgerüchten, über, den, bevorstehenden, Konkurs, von, Amazon, ,, setzt, die, Aktie, des, Online-Händlers, ihre, Talfahrt, fort, ., metadata={sent_id: "hdt-s2", text: "Begleitet von Marktgerüchten über den bevorstehenden Konkurs von Amazon , setzt die Aktie des Online-Händlers ihre Talfahrt fort ."}>,
  TokenList<An, der, Nasdaq, rutschte, das, Papier, am, an, dem, gestrigen, Mittwoch, kurz, sogar, unter, die, Marke, von, 10, US-Dollar, ,, in, Frankfurt, pendelt, sie, am, an, dem, heutigen, Donnerstag, zwischen, 10,40, und, 10,80, Euro, ., metadata={sent_id: "hdt-s3", text: "An der Nasdaq rutschte das Papier am gestrigen Mittwoch kurz sogar unter die Marke von 10 US-Dollar , in Frankfurt pendelt sie am heutigen Donnerstag zwischen 10,40 und 10,80 Euro ."}>,
  TokenList<Im, In, dem, Janu

In [4]:
nlp = spacy.load("de_core_news_sm")

with open("../../data/pseudowords/annotations.csv", "r") as csv_file:
    data = [row for row in csv.DictReader(csv_file)]
data

[{'uid': '57B9D1BEB68F44E7A51D1920F1EA6951E39469B5',
  'text': 'Und dann ist da noch das generelle Problem mit Hamas , dass nicht jeder Sprecher und Führer , der redet , auch etwas zu sagen , geschweige denn das letzte Wort hat .',
  'pos_tags': "['CCONJ', 'ADV', 'AUX', 'ADV', 'ADV', 'DET', 'ADJ', 'NOUN', 'ADP', 'PROPN', 'PUNCT', 'SCONJ', 'PART', 'ADJ', 'NOUN', 'CCONJ', 'NOUN', 'PUNCT', 'PRON', 'VERB', 'PUNCT', 'ADV', 'PRON', 'PART', 'VERB', 'PUNCT', 'CCONJ', 'ADV', 'DET', 'ADJ', 'NOUN', 'VERB', 'PUNCT']",
  'xpos_tags': '[]',
  'dep_rels': "['CC', 'ADVMOD', 'COP', 'ROOT', 'ADVMOD', 'DET', 'AMOD', 'NSUBJ', 'CASE', 'NMOD', 'PUNCT', 'MARK', 'ADVMOD:NEG', 'DET', 'NSUBJ', 'CC', 'CONJ', 'PUNCT', 'NSUBJ', 'ACL:RELCL', 'PUNCT', 'ADVMOD', 'OBJ', 'MARK', 'ACL', 'PUNCT', 'CC', 'ADVMOD', 'DET', 'AMOD', 'OBJ', 'CONJ', 'PUNCT']",
  'dep_heads': "['da', 'da', 'da', '.', 'da', 'problem', 'problem', 'da', 'hamas', 'problem', 'sagen', 'sagen', 'sagen', 'sprecher', 'sagen', 'führer', 'sprecher', 'redet'

In [5]:
# In case some attributes are not pre-annotated, add them using spaCy:
completed_data = []
for incomplete_example in tqdm(data):
    example = incomplete_example
    nlp_example = nlp(example["text"])
    example["construction_id"] = int(example["construction_id"])
    example["pos_tags"] = []  # eval(example["pos_tags"])
    example["xpos_tags"] = []  # eval(example["xpos_tags"])
    example["dep_rels"] = []  # eval(example["dep_rels"])
    example["dep_heads"] = []  # eval(example["dep_heads"])
    example["kees"] = eval(example["kees"])
    if len(example["pos_tags"]) == 0:
        example["pos_tags"] = [str(token.pos_) for token in nlp_example]
    if len(example["xpos_tags"]) == 0:
        example["xpos_tags"] = [str(token.tag_) for token in nlp_example]
    if len(example["dep_rels"]) == 0:
        example["dep_rels"] = [str(token.dep_).upper() for token in nlp_example]
    if len(example["dep_heads"]) == 0:
        example["dep_heads"] = [str(token.head).lower() for token in nlp_example]
    completed_data.append(example)
data = completed_data

data

  0%|          | 0/7028 [00:00<?, ?it/s]

[{'uid': '57B9D1BEB68F44E7A51D1920F1EA6951E39469B5',
  'text': 'Und dann ist da noch das generelle Problem mit Hamas , dass nicht jeder Sprecher und Führer , der redet , auch etwas zu sagen , geschweige denn das letzte Wort hat .',
  'pos_tags': ['CCONJ',
   'ADV',
   'AUX',
   'ADV',
   'ADV',
   'DET',
   'ADJ',
   'NOUN',
   'ADP',
   'PROPN',
   'PUNCT',
   'SCONJ',
   'PART',
   'DET',
   'NOUN',
   'CCONJ',
   'NOUN',
   'PUNCT',
   'PRON',
   'VERB',
   'PUNCT',
   'ADV',
   'PRON',
   'PART',
   'VERB',
   'PUNCT',
   'CCONJ',
   'ADV',
   'DET',
   'ADJ',
   'NOUN',
   'VERB',
   'PUNCT'],
  'xpos_tags': ['KON',
   'ADV',
   'VAFIN',
   'ADV',
   'ADV',
   'ART',
   'ADJA',
   'NN',
   'APPR',
   'NE',
   '$,',
   'KOUS',
   'PTKNEG',
   'PIAT',
   'NN',
   'KON',
   'NN',
   '$,',
   'PRELS',
   'VVFIN',
   '$,',
   'ADV',
   'PIS',
   'PTKZU',
   'VVINF',
   '$,',
   'KON',
   'ADV',
   'ART',
   'ADJA',
   'NN',
   'VAFIN',
   '$.'],
  'dep_rels': ['JU',
   'MO',
   'ROOT',

In [6]:
# Group the dataset into a list of lists where the label of the dictionaries is identical:
data.sort(key=lambda example: int(example["construction_id"]))  # Grouping doesn't work without sorting first!
data = {constr: list(group) for constr, group in itertools.groupby(data, key=lambda example: example["construction_id"])}

len(data)

210

In [7]:
list(data.keys())

[5,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 19,
 20,
 21,
 22,
 65,
 69,
 74,
 78,
 83,
 85,
 97,
 98,
 99,
 100,
 101,
 103,
 104,
 111,
 112,
 122,
 123,
 125,
 127,
 128,
 129,
 130,
 132,
 133,
 135,
 136,
 139,
 317,
 318,
 320,
 349,
 350,
 374,
 379,
 381,
 392,
 488,
 492,
 498,
 500,
 557,
 559,
 563,
 571,
 572,
 579,
 581,
 584,
 590,
 592,
 595,
 600,
 605,
 618,
 620,
 623,
 626,
 628,
 631,
 639,
 647,
 651,
 653,
 654,
 663,
 671,
 674,
 675,
 676,
 677,
 681,
 682,
 683,
 696,
 697,
 742,
 756,
 757,
 758,
 762,
 768,
 777,
 778,
 839,
 840,
 858,
 875,
 877,
 882,
 886,
 889,
 892,
 900,
 902,
 904,
 905,
 907,
 909,
 911,
 917,
 919,
 921,
 923,
 926,
 949,
 973,
 976,
 1004,
 1006,
 1029,
 1033,
 1034,
 1035,
 1043,
 1051,
 1054,
 1126,
 1134,
 1140,
 1162,
 1219,
 1257,
 1289,
 1291,
 1300,
 1301,
 1313,
 1315,
 1316,
 1320,
 1322,
 1323,
 1324,
 1329,
 1337,
 1342,
 1346,
 1347,
 1351,
 1459,
 1461,
 1462,
 1503,
 1509,
 1511,
 1514,
 1517,
 1521,
 1524,
 1525,
 1554,


We now try to exclude one sentence after the other to see if we can fill the empty sets.

In [8]:
def get_common_deps(constr, group):
    example_deps = []
    for example in group:
        # Variant with forms:
        tokens = [token for token in nlp(example["text"])]
        head_poss = [token.head.pos_ for token in nlp(example["text"])]
        head_tags = [token.head.tag_ for token in nlp(example["text"])]
        example_deps.append((example, tokens, head_poss, head_tags))
    
    num_excluded = len(group) - 2  # start with only two sentences which are left in the group
    common_deps = (set(), -1.0)
    
    while common_deps[1] != 0.0 and num_excluded > 0:
        last_common_deps = common_deps
        num_excluded -= 1
        exclude = itertools.combinations(range(len(group)), num_excluded)  # try to take away different sentences from the group
        
        # exclude sentences from the current group
        tries_left = 1000  # don't try for too long
        for exclude_list in exclude: # tqdm(exclude, desc=f"Exclude {num_excluded}", total=math.comb(len(group), num_excluded)):
            if tries_left == 0:
                break
            else:
                tries_left -= 1
            smaller_deps = example_deps.copy()
            if num_excluded > 0:
                for e in sorted(list(exclude_list), reverse=True):  # sorting like this makes sure there are no index errors
                    try: 
                        smaller_deps.pop(e)
                    except:
                        print(exclude_list)
            group_deps = []
            for example, tokens, head_poss, head_tags in smaller_deps:
                group_deps.append([
                    (str(token).lower(), str(dep), str(head))       # token -dep-> token
                    for token, dep, head in zip(tokens, example["dep_rels"], example["dep_heads"])
                ] + [
                    (str(tag), str(dep), str(head))         # tag -dep-> token
                    for tag, dep, head in zip(example["xpos_tags"], example["dep_rels"], example["dep_heads"])
                ] + [
                    (str(pos), str(dep), str(head))         # pos -dep-> token
                    for pos, dep, head in zip(example["pos_tags"], example["dep_rels"], example["dep_heads"])
                ] + [
                    (str(token).lower(), str(dep), str(head_tag))   # token -dep-> tag
                    for token, dep, head_tag in zip(tokens, example["dep_rels"], head_tags)
                ] + [
                    (str(tag), str(dep), str(head_tag))     # tag -dep-> tag
                    for tag, dep, head_tag in zip(example["xpos_tags"], example["dep_rels"], head_tags)
                ] + [
                    (str(pos), str(dep), str(head_tag))     # pos -dep-> tag
                    for pos, dep, head_tag in zip(example["pos_tags"], example["dep_rels"], head_tags)
                ] + [
                    (str(token).lower(), str(dep), str(head_pos))   # token -dep-> pos
                    for token, dep, head_pos in zip(tokens, example["dep_rels"], head_poss)
                ] + [
                    (str(tag), str(dep), str(head_pos))     # tag -dep-> pos
                    for tag, dep, head_pos in zip(example["xpos_tags"], example["dep_rels"], head_poss)
                ] + [
                    (str(pos), str(dep), str(head_pos))     # pos -dep-> pos
                    for pos, dep, head_pos in zip(example["pos_tags"], example["dep_rels"], head_poss)
                ])
                
            common_deps = set.intersection(*map(set, group_deps))
            common_deps = (common_deps, len(smaller_deps) / len(group)) if len(common_deps) > 0 else (common_deps, 0.0)
        
            if common_deps[1] < last_common_deps[1] :
                common_deps = last_common_deps
                break  # found the best common set
                
    with open("../../out/matches/matches_filters.tsv", "a+") as file:
        file.write(str(constr) + "\t" + str(1.0 - common_deps[1]) + "\t" + str(common_deps[0]) + "\t" + str(smaller_deps) + "\n")
    
    return constr, common_deps

In [ ]:
with open("../../out/matches/matches_filters.tsv", "w") as file:
    file.write("constr\tfuzziness\tfilter\tsentences used\n")
    
# common_deps = process_map(get_common_deps, data.items(), max_workers=4)

common_deps = {}
for constr, group in tqdm(data.items(), desc="Construction"):
    # try finding a common depencency
    common_deps[constr] = get_common_deps(constr, group)

Construction:   0%|          | 0/210 [00:00<?, ?it/s]

In [ ]:
# TODO Sortieren, KE-lex verpflichtend machen, und debuggen

matches = {}
scores = {}
for constr, (fuzziness, deps) in tqdm(common_deps.items()):
    matches[constr] = {}
    if set() in deps:
        continue
    for i, corpus_sentence in enumerate(all_ud_hdt_sentences): # in ud_hdt_sentences["de_hdt-ud-test.conllu"]
        missing = 0.0  # all group elements have to be found in the sentence, so let's check that in the end!
        for ex_token, ex_dep, ex_head in deps[0]:
            for token in corpus_sentence:
                if not token["head"]:  # for some reason, there is no token["head"] sometimes...
                    continue
                deptoken = str(token["form"]).lower()
                deptoken_xpos = str(token["xpos"]).lower()
                deptoken_upos = str(token["upos"]).lower()
                deprel = str(token["deprel"]).upper()
                dephead = str(corpus_sentence[token["head"]-1]["form"]).lower()
                dephead_xpos = corpus_sentence[token["head"]-1]["xpos"]
                dephead_upos = corpus_sentence[token["head"]-1]["upos"]
                    
                if (
                    ex_token in {deptoken, deptoken_xpos, deptoken_upos} and
                    ex_dep == deprel and
                    ex_head in {dephead, dephead_xpos, dephead_upos}
                ):
                    missing += 1.0
            if missing > 0.0:  # if any matches have been found
                with open(f"../../out/matches/graphics/{constr}_{i}.svg", "w") as out_file:
                    nlp_corpus_sentence = nlp(corpus_sentence.metadata["text"])
                    svg = displacy.render(nlp_corpus_sentence, style="dep", jupyter=False)
                    out_file.write(svg)
                # note the amount of fuzziness (how many examples have been used to create the common dependency set) and how many of them actually matched
                matches[constr][corpus_sentence.metadata["text"]] = (fuzziness, missing / float(len(deps)))

In [ ]:
matches.values()

In [ ]:
with open("../../out/matches/matches_dep_constr.tsv", "w") as file:
    file.write("constr\tfuzziness (common dep)\tfuzziness (matches)\tsentence\n")
    for key, match in matches.items(): 
        for sentence, score in match.items():
            file.write(str(key) + "\t" + str(score[0] * 100) + "\t" + str(score[1] * 100) + "\t" + sentence + "\n")

In [ ]:
import pickle

with open("../../out/matches/matches_dep_constr.pickle", "wb") as file:
    pickle.dump(matches, file)

In [ ]:
with open("../../out/matches/matches_dep_constr.pickle", "rb") as file:
    test = pickle.load(file)
test